# Jet Classification Exercise: Introduction to Machine Learning in High-Energy Physics

## Introduction to Classification

Classification is a fundamental task in machine learning where we aim to predict discrete class labels or categories for input data. In classification problems, we have:

- **Input features (X)**: The characteristics or measurements we use to make predictions
- **Target labels (y)**: The discrete categories we want to predict
- **Model**: A function that maps features to class probabilities or decisions

### Classification in High-Energy Physics: Jet Tagging

In high-energy physics, **jet tagging** is a crucial classification task where we identify the type of particle that initiated a jet of particles in a detector. Jets are collimated sprays of particles produced when high-energy quarks or gluons hadronize.

**Key applications:**
- **Top quark identification**: Distinguishing jets from top quark decay from background jets
- **Higgs boson searches**: Identifying jets from Higgs decay products
- **New physics searches**: Finding signatures of beyond-Standard-Model particles

**Why is this challenging?**
- High-dimensional feature space with complex correlations
- Large backgrounds from quantum chromodynamics (QCD) processes
- Need for high efficiency while maintaining low false positive rates
- Real-time processing requirements in detector trigger systems

This exercise focuses on **top quark jet tagging**, where we classify jets as either originating from top quark decay or from background QCD processes.

## Dataset Description: JetClass

We will use the **JetClass** dataset, a comprehensive dataset for jet classification tasks in high-energy physics.

**Dataset Reference:** https://zenodo.org/records/6619768

### Dataset Overview

The JetClass dataset contains simulated jet data with the following characteristics:

- **Purpose**: Multi-class jet classification (top, W/Z bosons, Higgs, QCD background)
- **Simulation**: Generated using Pythia8 Monte Carlo event generator
- **Detector**: CMS-like detector simulation with DELPHES
- **Jet Algorithm**: Anti-kT algorithm with $R$ = 0.4
- **Energy Range**: $\sqrt{s}$ = 13 TeV collision energy

### High-Level Observables

For this exercise, we focus on the following high-level observables:

1. $m_{\text{jet}}$: Soft-drop mass of the jet [GeV] - important for identifying massive particle decays
2. $\tau_N$: N-subjettiness variables that measure jet substructure
   - $\tau_1$: Measures how "1-pronged" a jet is
   - $\tau_2$: Measures how "2-pronged" a jet is  
   - $\tau_3$: Measures how "3-pronged" a jet is
   - $\frak{\tau_2/\tau_1}$ and $\frak{\tau_3/\tau_2}$: Key discriminating variables for top quark identification

### Physics Motivation

Top quarks have a distinctive decay signature:
- **Mass**: ~173 GeV (much heavier than light quarks)
- **Decay**: t -> W + b -> (q + q') + b (3-body final state)
- **Jet structure**: Creates a characteristic 3-pronged substructure in the jet

These features allow us to distinguish top quark jets from QCD background jets, which typically have different mass distributions and substructure patterns.

## Import Required Libraries

First, let's import all the necessary libraries for our analysis:

In [ ]:
# Python built-in libraries
import os
import urllib.request

# Third-party libraries
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from sklearn.metrics import auc, confusion_matrix, roc_curve
from torch.utils.data import DataLoader, TensorDataset

# Set random seeds for reproducibility
np.random.seed(42)
torch.manual_seed(42)

print("All libraries imported successfully!")

## Download Dataset

Let's download the JetClass dataset and save it to the `data/` directory. We will download a [preprocessed version](https://github.com/joschkabirk/jetclass-top-qcd/tree/main) of the dataset that contains high-level observables relevant for jet classification.

In [ ]:
# Create data directory if it doesn't exist
os.makedirs("data", exist_ok=True)

# Dataset URL and local path
url = "https://syncandshare.desy.de/index.php/s/5M56tM5KYAjq95o/download?path=%2F&files=filtered_jetclass_val.h5"
file_name = "data/jet_class.h5"

# Download the dataset if it doesn't already exist
if not os.path.exists(file_name):
    print(f"Downloading dataset from {url}")
    print("This may take a few minutes...")

    try:
        urllib.request.urlretrieve(url, file_name)
        print(f"Dataset successfully downloaded to {file_name}")
    except Exception as e:
        print(f"Error downloading dataset: {e}")
        print("Please check your internet connection and try again.")
else:
    print(f"Dataset already exists at {file_name}")

# Check file size
if os.path.exists(file_name):
    file_size = os.path.getsize(file_name) / (1024 * 1024)  # Convert to MB
    print(f"Dataset size: {file_size:.2f} MB")

## Load Dataset Using pandas

Now let's load the dataset using pandas and examine its structure:

In [ ]:
# Load the dataset
file_name = "data/jet_class.h5"

try:
    # Load the full dataset first to see available columns
    df_full = pd.read_hdf(file_name, key="df")
    print("Dataset loaded successfully!")
    print(f"Shape: {df_full.shape}")
    print(f"Available columns: {list(df_full.columns)}")

    # Select the columns we need for this exercise
    columns_needed = ["label_top", "jet_sdmass", "jet_tau1", "jet_tau2", "jet_tau3"]

    # Select only the columns we need
    df = df_full[columns_needed].copy()
    print(f"Selected features: {columns_needed}")
    print(f"Final dataset shape: {df.shape}")

    # Check class distribution
    print(f"Top quark jets: {df['label_top'].sum()}")
    print(f"Background jets: {len(df) - df['label_top'].sum()}")

except Exception as e:
    print(f"Error loading dataset: {e}")
    print("Please make sure the dataset has been downloaded correctly.")

## Plotting the Dataset

Let's visualize the key features to understand the differences between top quark jets and background jets:

In [ ]:
# Create derived features for plotting
df_plot = df.copy()
df_plot["tau2_over_tau1"] = df_plot["jet_tau2"] / df_plot["jet_tau1"]
df_plot["tau3_over_tau2"] = df_plot["jet_tau3"] / df_plot["jet_tau2"]

# Create a figure with subplots
fig, axes = plt.subplots(2, 2, figsize=(15, 12))
fig.suptitle("Jet Feature Distributions: Top Quark vs Background", fontsize=16, fontweight="bold")

# Define colors for the two classes
colors = ["orange", "blue"]
labels = ["Background (QCD)", "Top Quark"]

# Plot 1: Jet Mass Distribution
ax1 = axes[0, 0]
for i, label in enumerate([0, 1]):
    data = df_plot[df_plot["label_top"] == label]["jet_sdmass"]
    ax1.hist(data, bins=50, alpha=0.7, color=colors[i], label=labels[i], density=True)
ax1.set_xlabel("Jet Soft-Drop Mass [GeV]")
ax1.set_ylabel("Normalized Frequency")
ax1.set_title("Jet Mass Distribution")
ax1.legend()
ax1.grid(True, alpha=0.3)

# Plot 2: tau_2/tau_1 Distribution
ax2 = axes[0, 1]
# TODO: Add a histogram of tau_2/tau_1

# Plot 3: tau_3/tau_2 Distribution
ax3 = axes[1, 0]
# TODO: Add a histogram of tau_3/tau_2

# Plot 4: 2D scatter plot of tau ratios
ax4 = axes[1, 1]
# Sample data for better visualization (plot subset if dataset is large)
sample_size = min(5000, len(df_plot))
df_sample = df_plot.sample(n=sample_size, random_state=42)

for i, label in enumerate([0, 1]):
    data = df_sample[df_sample["label_top"] == label]
    tau21 = data["tau2_over_tau1"]
    tau32 = data["tau3_over_tau2"]

    # Filter for reasonable values
    mask = (tau21 > 0) & (tau21 < 1) & (tau32 > 0) & (tau32 < 1)
    ax4.scatter(tau21[mask], tau32[mask], alpha=0.5, color=colors[i], label=labels[i], s=10)

ax4.set_xlabel("tau_2/tau_1")
ax4.set_ylabel("tau_3/tau_2")
ax4.set_title("N-subjettiness Correlation")
ax4.legend()
ax4.grid(True, alpha=0.3)

plt.tight_layout()
plt.show()

TODO:
- What do you observe from the plots?
- Which physics features do you see in the distributions?
- How do the class differ and which features are most discriminative? Why?

## Convert to PyTorch Tensors and Preprocess the Data

Now let's prepare the data for training by converting to PyTorch tensors and applying preprocessing:

In [ ]:
# Prepare the features and target
# Create the feature matrix with derived features

# TODO: You can try to add more features like jet mass, ...
X = pd.DataFrame(
    {
        "jet_tau3": df["jet_tau3"],
        "tau2_over_tau1": df["jet_tau2"] / (df["jet_tau1"] + 1e-8),
    }
)
y = df["label_top"]

print(f"Features: {list(X.columns)}")
print(f"Target: {y.name}")

# Convert to PyTorch tensors
X_tensor = torch.from_numpy(X.values)
y_tensor = torch.from_numpy(y.values)

# Standardize features (important for neural networks)
means = X_tensor.mean(axis=0, keepdim=True)
stds = X_tensor.std(axis=0, keepdims=True)
X_tensor = (X_tensor - means) / stds

# Convert datatype
X_tensor = X_tensor.to(torch.float32, copy=False)
y_tensor = y_tensor.to(torch.int64, copy=False)

print("\nPyTorch tensor shapes:")
print(f"X_tensor: {X_tensor.shape}")
print(f"y_tensor: {y_tensor.shape}")
print(f"X_tensor dtype: {X_tensor.dtype}")
print(f"y_tensor dtype: {y_tensor.dtype}")

## Train/Validation/Test Split

Let's split our data into training, validation, and test sets:

In [ ]:
# Split the data: 70% train, 15% validation, 15% test
num_samples = X_tensor.shape[0]
indices = torch.randperm(num_samples)

# Compute split sizes
train_end = int(0.7 * num_samples)
val_end = int(0.85 * num_samples)

train_idx = indices[:train_end]
val_idx = indices[train_end:val_end]
test_idx = indices[val_end:]

X_train, y_train = X_tensor[train_idx], y_tensor[train_idx]
X_val, y_val = X_tensor[val_idx], y_tensor[val_idx]
X_test, y_test = X_tensor[test_idx], y_tensor[test_idx]

# Check class distribution in each split
print("\nClass distribution:")
for name, y_split in [("Train", y_train), ("Validation", y_val), ("Test", y_test)]:
    top_ratio = y_split.float().mean()
    print(f"{name}: {top_ratio:.3f} top quark ratio ({y_split.sum()}/{len(y_split)})")

# Create DataLoaders for efficient batch processing
batch_size = 256

train_dataset = TensorDataset(X_train, y_train)
val_dataset = TensorDataset(X_val, y_val)
test_dataset = TensorDataset(X_test, y_test)

train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False)
test_loader = DataLoader(test_dataset, batch_size=batch_size, shuffle=False)

print(f"\nDataLoaders created with batch size: {batch_size}")
print(f"Training batches: {len(train_loader)}")
print(f"Validation batches: {len(val_loader)}")
print(f"Test batches: {len(test_loader)}")

## Define a Simple Neural Network Model Using torch.nn

Let's create a feedforward neural network for binary classification:

In [ ]:
class JetClassifier(nn.Module):

    def __init__(self, input_size, num_classes=2):
        super().__init__()

        # Hidden layers
        self.fc1 = nn.Linear(input_size, 4)
        # TODO: Try to add two more layers/neurons
        # self.fc2 =
        # self.fc3 =

        self.act = nn.ReLU()

        # TODO: watch out for the sizes
        self.out = nn.Linear(4, num_classes)

    def forward(self, x):
        """Forward pass through the network"""
        # Apply each layer with activation
        x = self.fc1(x)
        x = self.act(x)

        # TODO: The layers must be applied here
        # ....

        x = self.out(x)  # Output layer (no activation here, will use CrossEntropyLoss)

        return x

In [ ]:
# Get the input size from our feature tensor
input_size = X_train.shape[1]

# Create the model
model = JetClassifier(input_size=input_size, num_classes=2)

# Print model architecture
print("Model Architecture:")
print(model)

# Count parameters
total_params = sum(p.numel() for p in model.parameters())
trainable_params = sum(p.numel() for p in model.parameters() if p.requires_grad)

print("\nModel Summary:")
print(f"Input features: {input_size}")
print(f"Total parameters: {total_params:,}")
print(f"Trainable parameters: {trainable_params:,}")

# Test the model with a small batch
with torch.no_grad():
    test_input = X_train[:5]  # First 5 samples
    test_output = model(test_input)
    print("\nTest forward pass:")
    print(f"Input shape: {test_input.shape}")
    print(f"Output shape: {test_output.shape}")
    print(f"Output (logits):\n{test_output}")

## Train the Model Using torch.optim and torch.nn.CrossEntropyLoss

Now let's train our neural network:

In [ ]:
# Training parameters
# TODO: Try different values for these parameters
num_epochs = 5
early_stopping_patience = 5
learning_rate = 0.00001
weight_decay = 0.0  # L2 regularization

# Define loss function and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(
    model.parameters(),
    lr=learning_rate,
    weight_decay=weight_decay,
)

# Early stopping parameters
best_val_loss = float("inf")
patience_counter = 0

# Lists to store training history
train_losses = []
val_losses = []
train_accuracies = []
val_accuracies = []

print("Starting training...")
print(
    f"Training for {num_epochs} epochs with early stopping (patience: {early_stopping_patience})"
)

for epoch in range(num_epochs):
    # Training phase
    model.train()
    train_loss = 0.0
    train_correct = 0
    train_total = 0

    for batch_X, batch_y in train_loader:
        # Zero the gradients
        optimizer.zero_grad()

        # Forward pass
        outputs = model(batch_X)
        loss = criterion(outputs, batch_y)

        # Backward pass and optimization
        loss.backward()
        optimizer.step()

        # Statistics
        train_loss += loss.item()
        _, predicted = torch.max(outputs.data, 1)
        train_total += batch_y.size(0)
        train_correct += (predicted == batch_y).sum().item()

    # Validation phase
    model.eval()
    val_loss = 0.0
    val_correct = 0
    val_total = 0

    with torch.no_grad():
        for batch_X, batch_y in val_loader:
            outputs = model(batch_X)
            loss = criterion(outputs, batch_y)

            val_loss += loss.item()
            _, predicted = torch.max(outputs.data, 1)
            val_total += batch_y.size(0)
            val_correct += (predicted == batch_y).sum().item()

    # Calculate epoch metrics
    epoch_train_loss = train_loss / len(train_loader)
    epoch_val_loss = val_loss / len(val_loader)
    epoch_train_acc = 100 * train_correct / train_total
    epoch_val_acc = 100 * val_correct / val_total

    # Store metrics
    train_losses.append(epoch_train_loss)
    val_losses.append(epoch_val_loss)
    train_accuracies.append(epoch_train_acc)
    val_accuracies.append(epoch_val_acc)

    # Print progress
    print(f"Epoch [{epoch+1}/{num_epochs}]")
    print(f"  Train Loss: {epoch_train_loss:.4f}, Train Acc: {epoch_train_acc:.2f}%")
    print(f"  Val Loss: {epoch_val_loss:.4f}, Val Acc: {epoch_val_acc:.2f}%")

    # Early stopping
    if epoch_val_loss < best_val_loss:
        best_val_loss = epoch_val_loss
        patience_counter = 0
        # Save the best model
        best_model_state = model.state_dict().copy()
    else:
        patience_counter += 1

    if patience_counter >= early_stopping_patience:
        print(f"\nEarly stopping triggered after epoch {epoch+1}")
        print(f"Best validation loss: {best_val_loss:.4f}")
        break

# Load the best model
model.load_state_dict(best_model_state)
print(f"\nTraining completed! Best validation loss: {best_val_loss:.4f}")

In [ ]:
# Plot training history
fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15, 5))

# Plot loss
epochs = range(1, len(train_losses) + 1)
ax1.plot(epochs, train_losses, "b-", label="Training Loss", linewidth=2)
ax1.plot(epochs, val_losses, "r-", label="Validation Loss", linewidth=2)
ax1.set_title("Model Loss During Training")
ax1.set_xlabel("Epoch")
ax1.set_ylabel("Loss")
ax1.set_ylim([0.35, 0.7])
ax1.legend()
ax1.grid(True, alpha=0.3)

# Plot accuracy
ax2.plot(epochs, train_accuracies, "b-", label="Training Accuracy", linewidth=2)
ax2.plot(epochs, val_accuracies, "r-", label="Validation Accuracy", linewidth=2)
ax2.set_title("Model Accuracy During Training")
ax2.set_xlabel("Epoch")
ax2.set_ylabel("Accuracy (%)")
ax2.set_ylim([50, 100])
ax2.legend()
ax2.grid(True, alpha=0.3)

plt.tight_layout()
plt.show()

# Print final training statistics
print("Final Training Results:")
print(f"Training Accuracy: {train_accuracies[-1]:.2f}%")
print(f"Validation Accuracy: {val_accuracies[-1]:.2f}%")
print(f"Training Loss: {train_losses[-1]:.4f}")
print(f"Validation Loss: {val_losses[-1]:.4f}")

## Evaluate the Model on the Test Set

Let's evaluate our trained model on the test set to get unbiased performance metrics:

In [ ]:
# Evaluate on test set
model.eval()
test_predictions = []
test_probabilities = []
test_labels = []

with torch.no_grad():
    for batch_X, batch_y in test_loader:
        outputs = model(batch_X)
        probabilities = F.softmax(outputs, dim=1)
        _, predicted = torch.max(outputs, 1)

        test_predictions.append(predicted.numpy())
        test_probabilities.append(probabilities.numpy())
        test_labels.append(batch_y.numpy())

# Concatenate batched results
test_predictions = np.concatenate(test_predictions)
test_probabilities = np.concatenate(test_probabilities)
test_labels = np.concatenate(test_labels)

# Calculate test accuracy
test_accuracy = (test_predictions == test_labels).mean() * 100

print("Test Set Evaluation Results:")
print(f"Test Accuracy: {test_accuracy:.2f}%")
print(f"Number of test samples: {len(test_labels)}")

## Visualize the Results (Confusion Matrix, ROC Curve)

Let's create visualizations to better understand our model's performance:

In [ ]:
# Create visualizations
fig, axes = plt.subplots(1, 3, figsize=(18, 5))

# 1. Confusion Matrix
cm = confusion_matrix(test_labels, test_predictions)
sns.heatmap(
    cm,
    annot=True,
    fmt="d",
    cmap="Blues",
    xticklabels=["Background", "Top Quark"],
    yticklabels=["Background", "Top Quark"],
    ax=axes[0],
)
axes[0].set_title("Confusion Matrix")
axes[0].set_xlabel("Predicted Label")
axes[0].set_ylabel("True Label")

# Add percentage annotations
total = cm.sum()
for i in range(2):
    for j in range(2):
        percentage = cm[i, j] / total * 100
        axes[0].text(
            j + 0.5,
            i + 0.7,
            f"({percentage:.1f}%)",
            ha="center",
            va="center",
            fontsize=10,
            color="red",
        )

# 2. ROC Curve
fpr, tpr, thresholds = roc_curve(test_labels, test_probabilities[:, 1])
roc_auc = auc(fpr, tpr)

axes[1].plot(fpr, tpr, color="darkorange", lw=2, label=f"ROC Curve (AUC = {roc_auc:.3f})")
axes[1].plot([0, 1], [0, 1], color="navy", lw=2, linestyle="--", alpha=0.5)
axes[1].set_xlim([0.0, 1.0])
axes[1].set_ylim([0.0, 1.05])
axes[1].set_xlabel("False Positive Rate (1 - Specificity)")
axes[1].set_ylabel("True Positive Rate (Sensitivity)")
axes[1].set_title("Receiver Operating Characteristic (ROC) Curve")
axes[1].legend(loc="lower right")
axes[1].grid(True, alpha=0.3)

# 3. Prediction Probability Distribution
prob_top = test_probabilities[:, 1]  # Probability of being a top quark
prob_background = prob_top[test_labels == 0]  # Background jets
prob_signal = prob_top[test_labels == 1]  # Top quark jets

axes[2].hist(
    prob_background, bins=50, alpha=0.7, label="Background (QCD)", color="orange", density=True
)
axes[2].hist(prob_signal, bins=50, alpha=0.7, label="Top Quark", color="blue", density=True)
axes[2].axvline(x=0.5, color="red", linestyle="--", alpha=0.8, label="Decision Threshold (0.5)")
axes[2].set_xlabel("Predicted Probability (Top Quark)")
axes[2].set_ylabel("Density")
axes[2].set_title("Prediction Probability Distribution")
axes[2].legend()
axes[2].grid(True, alpha=0.3)

plt.tight_layout()
plt.show()

In [ ]:
# TODO: here you can plot the SIC (Significance Improvement Characteristic) curve.
# the SIC values are defined as TPR / sqrt(FPR) where TPR stands for true positive rate and FRP for false positive rate
# x-axis: TPR , y-axis: SIC value